# Prevendo roubo de celulares em SP

O trabalho do [Lucas Moretto](https://github.com/LucasMorettoRodrigues/roubo_de_celular_em_SP) será a base para nossa análise e proposta de solução.

Esta análise será realizada com dados de 2010 a 2018 pois o site da Secretaria de Segurança Pública de São Paulo (SSP-SP) demora bastante para responder uma requisição (10-40 min) e por vezes a conexão com o servidor cai.


## Baixando bibliotecas necessárias

`conda install numpy pandas xlwt xlrd plotly matplotlib`


`conda install -c conda-forge squarify`

### Importando bibliotecas necessárias

In [1]:
import pandas as pd
import numpy as np
import glob  
import plotly.graph_objs as go
import plotly.offline as py
import matplotlib.pyplot as plt               # Visualização de dados
import matplotlib
plt.style.use('fivethirtyeight') 
import squarify
from datetime import datetime
from folium import Map
from folium.plugins import HeatMap

### Abrindo arquivo XLS disponível no SSP-SP

#### Os arquivos possuem um erro, sendo impossível abrir o arquivo
*XLRDError: Unsupported format, or corrupt file: Expected BOF record; found b'A\x00N\x00O\x00_\x00'*

A solução foi encontrada nesse artigo do [Medium](https://medium.com/@jerilkuriakose/recover-corrupt-excel-file-xls-or-xlsx-using-python-2eea6bb07aae)

#### Apenas para resolver o problema de formato
from __future__ import unicode_literals deve ser importado pouco antes da abertura do arquivo

In [2]:
from __future__ import unicode_literals
from xlwt import Workbook
import io

def solve_xls(filename = 'datasets/DadosBO_2020_8.xls'):

    file = io.open(filename, "r", encoding="utf-16-le")
    data = file.readlines()
    xldoc = Workbook()
    
    sheet = xldoc.add_sheet("Sheet1", cell_overwrite_ok=True)
    
    for i, row in enumerate(data):
        for j, val in enumerate(row.replace('\n', '').split('\t')):
            sheet.write(i, j, val)
    xldoc.save('file.xls')

## Análise Mês de Agosto 2020

In [2]:
dateparse = lambda x: datetime.strptime(x, '%d/%m/%Y')

columns = ['ANO_BO', 'NUM_BO', 'DATAOCORRENCIA', 'HORAOCORRENCIA', 'PERIDOOCORRENCIA', 'DATACOMUNICACAO', 'BO_AUTORIA', 'FLAGRANTE', 'LOGRADOURO', 'NUMERO', 'BAIRRO', 'CIDADE', 'UF', 'LATITUDE', 'LONGITUDE', 'DESCRICAOLOCAL', 'DESCR_TIPO_VEICULO', 'SOLUCAO', 'DELEGACIA_NOME', 'DELEGACIA_CIRCUNSCRICAO', 'ESPECIE', 'RUBRICA', 'DESDOBRAMENTO', 'STATUS', 'QUANT_CELULAR', 'MARCA_CELULAR']

#column_dates = ['DATAOCORRENCIA', 'DATACOMUNICACAO']
column_dates = ['DATACOMUNICACAO']

dtypes = {
    'ANO_BO': np.int32,
    'NUM_BO': np.int64,
    'QUANT_CELULAR': pd.Int16Dtype(),
    'LATITUDE': np.float32,
    'LONGITUDE': np.float32 
}

dataset = pd.read_excel("datasets/file.xls", usecols=columns, dtype=dtypes, parse_dates=column_dates, date_parser=dateparse, thousands=',')

#### Antes da eliminação das duplicatas

In [3]:
before_drop = dataset.shape[0]
print("Quantidade de tuplas: ",dataset.shape[0])

Quantidade de tuplas:  13532


#### Eliminando duplicatas de acordo com [Metodologia](https://drive.google.com/file/d/1_CBHVulHPzLzRyCNpxGXSECVDV-u21QH/view)

In [4]:
dataset.drop_duplicates(subset=['DELEGACIA_NOME', 'ANO_BO', 'NUM_BO'], inplace=True)
dataset.reset_index(drop=True,inplace=True)

In [5]:
dataset['HORARIOOCORRENCIA'] = pd.to_datetime(dataset.DATAOCORRENCIA + ' ' + dataset.HORAOCORRENCIA)

In [6]:
dataset['DATAOCORRENCIA'] = pd.to_datetime(dataset['DATAOCORRENCIA'], format='%d/%m/%Y')

#### Após remoção das duplicatas

In [7]:
after_drop = dataset.shape[0]
print("Quantidade de tuplas: ",dataset.shape[0])

Quantidade de tuplas:  11071


#### Percentual de redução no dataset:

In [8]:
print("Redução de: ", 100-(after_drop/before_drop)*100)

Redução de:  18.18652083949158


#### Maioria das ocorrências não são flagrante

In [9]:
print('Quantidade de ocorrências que é flagrante: ',dataset[dataset["FLAGRANTE"]=="Sim"].shape[0])

Quantidade de ocorrências que é flagrante:  115


In [10]:
dataset.dtypes

ANO_BO                              int32
NUM_BO                              int64
DATAOCORRENCIA             datetime64[ns]
HORAOCORRENCIA                     object
PERIDOOCORRENCIA                   object
DATACOMUNICACAO            datetime64[ns]
BO_AUTORIA                         object
FLAGRANTE                          object
LOGRADOURO                         object
NUMERO                            float64
BAIRRO                             object
CIDADE                             object
UF                                 object
LATITUDE                          float32
LONGITUDE                         float32
DESCRICAOLOCAL                     object
SOLUCAO                            object
DELEGACIA_NOME                     object
DELEGACIA_CIRCUNSCRICAO            object
ESPECIE                            object
RUBRICA                            object
DESDOBRAMENTO                      object
STATUS                             object
DESCR_TIPO_VEICULO                

#### Converter coluna com horario da ocorrencia para segundos

In [11]:
dataset['timestamp_ocorrencia'] = dataset['HORARIOOCORRENCIA'].dt.hour*3600 + dataset['HORARIOOCORRENCIA'].dt.minute*60 + dataset['HORARIOOCORRENCIA'].dt.second

#### Horário médio de ocorrência de crimes por turno(manhã, tarde, noite, madrugada)

In [12]:
import datetime
manha = dataset[dataset['PERIDOOCORRENCIA']=="PELA MANHÃ"]['timestamp_ocorrencia'].mean()
str(datetime.timedelta(seconds=manha))

'8:35:17.313975'

In [13]:
tarde = dataset[dataset['PERIDOOCORRENCIA']=="A TARDE"]['timestamp_ocorrencia'].mean()
str(datetime.timedelta(seconds=tarde))

'15:03:48.471616'

In [14]:
noite = dataset[dataset['PERIDOOCORRENCIA']=="A NOITE"]['timestamp_ocorrencia'].mean()
str(datetime.timedelta(seconds=noite))

'20:38:43.968711'

In [15]:
madrugada = dataset[dataset['PERIDOOCORRENCIA']=="DE MADRUGADA"]['timestamp_ocorrencia'].mean()
str(datetime.timedelta(seconds=madrugada))

'3:33:57.629630'

In [17]:
len(dataset['timestamp_ocorrencia'].unique())

756

#### Top 5 horários com maior incidência de crimes por turno

In [18]:
dataset[dataset['PERIDOOCORRENCIA']=="A TARDE"].nlargest(5, "timestamp_ocorrencia")

ANO_BO   NUM_BO DATAOCORRENCIA HORAOCORRENCIA PERIDOOCORRENCIA  \
9489     2020  1231737     2020-08-23          17:55          A TARDE   
10371    2020  1244867     2020-08-29          17:55          A TARDE   
278      2020  1073645     2020-08-01          17:51          A TARDE   
6        2020  1069205     2020-07-31          17:50          A TARDE   
866      2020  1083670     2020-08-03          17:50          A TARDE   

      DATACOMUNICACAO    BO_AUTORIA FLAGRANTE  \
9489       2020-08-27  Desconhecida       Não   
10371      2020-08-29  Desconhecida       Não   
278        2020-08-01  Desconhecida       Não   
6          2020-07-31  Desconhecida       Não   
866        2020-08-03  Desconhecida       Não   

                                LOGRADOURO   NUMERO  ...  \
9489                     AVENIDA SAPOPEMBA  10828.0  ...   
10371                   RUA MAESTRO CARDIM    950.0  ...   
278    AVENIDA MARECHAL DEODORO DA FONSECA   1520.0  ...   
6                        ALAMEDA CLEVELAND    331.0  ...   
866              RUA GUSTAV WILLI BORGHOFF    700.0  ...   

      DELEGACIA_CIRCUNSCRICAO                                   ESPECIE  \
9489        70º D.P. VILA EMA  Título II - Patrimônio (arts. 155 a 183)   
10371      05º D.P. ACLIMACAO  Título II - Patrimônio (arts. 155 a 183)   
278           DEL.POL.GUARUJA  Título II - Patrimônio (arts. 155 a 183)   
6      77º D.P. SANTA CECILIA  Título II - Patrimônio (arts. 155 a 183)   
866         23º D.P. PERDIZES  Título II - Patrimônio (arts. 155 a 183)   

                             RUBRICA  DESDOBRAMENTO     STATUS  \
9489       Roubo (art. 157) - OUTROS            NaN  Consumado   
10371      Roubo (art. 157) - OUTROS            NaN  Consumado   
278        Roubo (art. 157) - OUTROS            NaN  Consumado   
6          Roubo (art. 157) - OUTROS            NaN  Consumado   
866    Roubo (art. 157) - TRANSEUNTE            NaN  Consumado   

      DESCR_TIPO_VEICULO QUANT_CELULAR MARCA_CELULAR   HORARIOOCORRENCIA  \
9489                 NaN          <NA>         APPLE 2020-08-23 17:55:00   
10371                NaN          <NA>       SAMSUNG 2020-08-29 17:55:00   
278                  NaN          <NA>         APPLE 2020-01-08 17:51:00   
6                    NaN          <NA>       SAMSUNG 2020-07-31 17:50:00   
866                  NaN          <NA>      MOTOROLA 2020-03-08 17:50:00   

      timestamp_ocorrencia  
9489               64500.0  
10371              64500.0  
278                64260.0  
6                  64200.0  
866                64200.0  

[5 rows x 28 columns]

#### Média de dias para comunicar a policia sobre o roubo

In [19]:
dataset['DATAOCORRENCIA'] = dataset['DATAOCORRENCIA'].astype('datetime64')
dataset['DATACOMUNICACAO'] = dataset['DATACOMUNICACAO'].astype('datetime64')

In [20]:
dias = (dataset['DATACOMUNICACAO'] - dataset['DATAOCORRENCIA'])/ np.timedelta64(1, 'D')

In [21]:
somatorio = 0
for item in dias:
    if item < 180:
        somatorio = somatorio + item

In [22]:
somatorio = somatorio/len(dias)
print("Tempo medio(em dias) que uma vitima abre um BO:",somatorio)

Tempo medio(em dias) que uma vitima abre um BO: 2.6479089513142444


## Carregando dados de 2010 a 2020 (agosto)

In [27]:
# FUNÇÃO PARA IMPORTAR DATASET

dir_path = "data/"

def importaData(files):
    
    data = dir_path + files
    allFiles = glob.glob('data/*.csv')
    list_ = []
    dtypes = {
        'ANO_BO': object,
        'NUM_BO': object,
        'DATAOCORRENCIA': object,
        'PERIDOOCORRENCIA':object,
        'BAIRRO':object,
        'CIDADE':object,
        'LATITUDE':object,
        'LONGITUDE':object,
        'LOGRADOURO':object,
        'DESCRICAOLOCAL':object,
        'DESCR_TIPO_VEICULO':object,
        'DELEGACIA_NOME': object,
        'QUANT_CELULAR': object
    }
    cols = ['ANO_BO', 'NUM_BO', 'DATAOCORRENCIA', 'PERIDOOCORRENCIA', 'BAIRRO', 'CIDADE', 'LATITUDE', 'LONGITUDE', 'LOGRADOURO', \
           'DESCRICAOLOCAL', 'DESCR_TIPO_VEICULO', 'DELEGACIA_NOME',  'QUANT_CELULAR']

    for file_ in allFiles:
        df = pd.read_csv(file_,index_col=None, header=0, delimiter=';', usecols=cols, dtype=dtypes, thousands=',')
        list_.append(df)

    df = pd.concat(list_, axis = 0, ignore_index = True)
    return df

# IMPORTANDO DATASET

dataset = importaData('*.csv')

In [28]:
dataset.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1709458 entries, 0 to 1709457
Data columns (total 13 columns):
 #   Column              Dtype 
---  ------              ----- 
 0   ANO_BO              object
 1   NUM_BO              object
 2   DATAOCORRENCIA      object
 3   PERIDOOCORRENCIA    object
 4   LOGRADOURO          object
 5   BAIRRO              object
 6   CIDADE              object
 7   LATITUDE            object
 8   LONGITUDE           object
 9   DESCRICAOLOCAL      object
 10  DELEGACIA_NOME      object
 11  DESCR_TIPO_VEICULO  object
 12  QUANT_CELULAR       object
dtypes: object(13)
memory usage: 169.5+ MB


In [29]:
# REMOVENDO DADOS DUPLICADOS

def removeDuplicados(df):
    df.drop_duplicates(subset=['DELEGACIA_NOME', 'ANO_BO', 'NUM_BO'], inplace=True)
    df.reset_index(drop=True,inplace=True)
    return df

dataset = removeDuplicados(dataset)
dataset.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1278175 entries, 0 to 1278174
Data columns (total 13 columns):
 #   Column              Non-Null Count    Dtype 
---  ------              --------------    ----- 
 0   ANO_BO              1278175 non-null  object
 1   NUM_BO              1278175 non-null  object
 2   DATAOCORRENCIA      1278172 non-null  object
 3   PERIDOOCORRENCIA    1278174 non-null  object
 4   LOGRADOURO          1224442 non-null  object
 5   BAIRRO              1093579 non-null  object
 6   CIDADE              1235274 non-null  object
 7   LATITUDE            1090572 non-null  object
 8   LONGITUDE           1090570 non-null  object
 9   DESCRICAOLOCAL      1278173 non-null  object
 10  DELEGACIA_NOME      1278172 non-null  object
 11  DESCR_TIPO_VEICULO  162023 non-null   object
 12  QUANT_CELULAR       932206 non-null   object
dtypes: object(13)
memory usage: 126.8+ MB


### Tratando os dados temporais
Aqui fazemos a remoção de tuplas com data inferior ao ano de 2010. Alguns podem ser erro de digitação mas a maioria dos dados que não se enquadram são de outros anos (década de 90 até 2009).

In [26]:
# dataset['DATAOCORRENCIA'] = pd.to_datetime(dataset['DATAOCORRENCIA'], format='%d/%m/%Y', errors='coerce')
# for row in dataset['DATAOCORRENCIA'].items():
#     if row[1] < pd.datetime(2010, 1, 1):
#         print(row[1])

In [30]:
# TRANSFORMANDO DADOS TEMPORAIS

def tratarDatas(df, col = 'DATAOCORRENCIA'):
    df[col] = pd.to_datetime(df[col], format='%d/%m/%Y', errors='coerce')
    indexs = []
    for row in df[col].items():
        if row[1] < pd.datetime(2010, 1, 1):
            indexs.append(row[0])
    df.drop(index=indexs, axis=1, inplace=True)
    df['diasemana'] = df[col].dt.day_name()
    df['mesano'] = df[col].dt.strftime('%Y-%m')
    df['ano'] = df[col].dt.strftime('%Y')
    df['mes'] = df[col].dt.month
    #df.drop(index=df[df['mesano'] == 'NaT'].index, inplace=True, axis=0)
    return df
    
dataset = tratarDatas(dataset)

/home/everson/miniconda3/envs/env/lib/python3.7/site-packages/ipykernel_launcher.py:7: FutureWarning:

The pandas.datetime class is deprecated and will be removed from pandas in a future version. Import from datetime module instead.



In [31]:
dataset.reset_index(drop='index',inplace=True)

In [32]:
dataset

ANO_BO  NUM_BO DATAOCORRENCIA PERIDOOCORRENCIA  \
0         2011    4486     2011-05-31          A NOITE   
1         2011    2222     2011-06-01     DE MADRUGADA   
2         2011    2447     2011-05-31          A NOITE   
3         2011    2282     2011-05-31          A NOITE   
4         2011    4331     2011-05-31          A NOITE   
...        ...     ...            ...              ...   
1276176   2015  542079     2015-04-30       PELA MANHÃ   
1276177   2015  541976     2015-04-30          A NOITE   
1276178   2015  542132     2015-04-30          A NOITE   
1276179   2015  542117     2015-04-30          A NOITE   
1276180   2015    1785     2015-04-30          A NOITE   

                              LOGRADOURO               BAIRRO   CIDADE  \
0                                    NaN                  NaN      NaN   
1                      R ANTONIO GANDINI  CONJ.JOSE BONIFACIO  S.PAULO   
2                                    NaN                  NaN      NaN   
3                      RUA DA CONSOLACAO               CENTRO  S.PAULO   
4                   R BENEDITO BERNARDES             VILA EMA  S.PAULO   
...                                  ...                  ...      ...   
1276176          Rua Conselheiro Ramalho           BELA VISTA  S.PAULO   
1276177              RUA AFONSO ALIPERTI           Agua funda  S.PAULO   
1276178                 AVENIDA VILA EMA        VILA PRUDENTE  S.PAULO   
1276179  RUA AGOSTINHO DA SILVA MONTEIRO          vila curuça  S.PAULO   
1276180                    RUA SAO ROQUE            SAPOPEMBA  S.PAULO   

             LATITUDE     LONGITUDE DESCRICAOLOCAL            DELEGACIA_NOME  \
0                 NaN           NaN     Residência          30º D.P. TATUAPE   
1        -23,54134985  -46,44580638    Via pública  103º D.P. COHABII/ITAQU.   
2                 NaN           NaN     Residência  53º D.P. PARQUE DO CARMO   
3        -23,54834522  -46,64717688    Via pública         DEL.POL.MAIRIPORÃ   
4        -23,58082417  -46,54311025    Via pública      56º D.P. VILA ALPINA   
...               ...           ...            ...                       ...   
1276176           NaN           NaN         Outros      DELEGACIA ELETRONICA   
1276177  -23,63480333  -46,62051526         Outros      DELEGACIA ELETRONICA   
1276178  -23,57762416  -46,57590088         Outros      DELEGACIA ELETRONICA   
1276179  -23,49522395  -46,41121509         Outros      DELEGACIA ELETRONICA   
1276180  -23,60317521  -46,52392589    Via pública         70º D.P. VILA EMA   

        DESCR_TIPO_VEICULO QUANT_CELULAR  diasemana   mesano   ano  mes  
0               UTILITÁRIO             1    Tuesday  2011-05  2011  5.0  
1                      NaN           NaN  Wednesday  2011-06  2011  6.0  
2                AUTOMOVEL             1    Tuesday  2011-05  2011  5.0  
3                      NaN             1    Tuesday  2011-05  2011  5.0  
4                      NaN           NaN    Tuesday  2011-05  2011  5.0  
...                    ...           ...        ...      ...   ...  ...  
1276176                NaN             1   Thursday  2015-04  2015  4.0  
1276177          AUTOMOVEL             1   Thursday  2015-04  2015  4.0  
1276178                NaN             1   Thursday  2015-04  2015  4.0  
1276179                NaN             1   Thursday  2015-04  2015  4.0  
1276180                NaN             1   Thursday  2015-04  2015  4.0  

[1276181 rows x 17 columns]

## Análise Gráfica

### Ano com maior ocorrência de roubos de celular
Dentre os anos presentes no dataset, o mais preocupante é o ano de 2014. Dados sempre tem algo para nos ensinar e neste caso, o ano com maior incidência de crimes pode nos dizer algo em uma análise temporal.

In [33]:
ocorrencias = dataset.groupby('ano').count()['ANO_BO'].reset_index()
ocorrencias[ocorrencias['ANO_BO']==max(ocorrencias['ANO_BO'])]

ano  ANO_BO
9  2019  206611

In [34]:
ocorrencias = dataset[dataset['ano']=='2019'].groupby('mesano').count()['ANO_BO'].reset_index()
ocorrencias.rename(columns={'mesano': 'Data', 'ANO_BO':'Ocorrências de Roubo de Celular'}, inplace=True)

In [36]:
trace = [go.Scatter(x = ocorrencias.Data, y = ocorrencias['Ocorrências de Roubo de Celular'])]

layout = dict(
    title='Ocorrências de Roubo de Celular Ano 2019',
    yaxis=dict(
    title='Ocorrências'
    ),
    xaxis=dict(
        rangeslider=dict(
            visible = True
        ),
        type='date'
    )
)

fig = dict(data=trace, layout=layout)
py.iplot(fig)

In [37]:
dataset['diasemana'] = pd.Categorical(dataset['diasemana'], categories=['Monday','Tuesday','Wednesday','Thursday','Friday','Saturday', 'Sunday'], ordered=True)

In [38]:
trace = [go.Bar(
            x = dataset[dataset['ANO_BO']=='2019']['diasemana'].value_counts().sort_index().index,
            y = dataset[dataset['ANO_BO']=='2019']['diasemana'].value_counts().sort_index().values,
            textposition = 'auto',
            marker=dict(
                color='rgb(158,202,225)',
                line=dict(
                    color='rgb(8,48,107)',
                    width=1,
                    )
                ),
            opacity=0.8
)]
           
layout = go.Layout(
    title='Roubo de Celular por Dia da Semana ano 2019',
    yaxis=dict(
        title='Ocorrências'
        ),
)

fig = go.Figure(data=trace, layout=layout)

py.iplot(fig)

Turno do dia - Excluindo período 'EM HORA INCERTA'

In [42]:
dataset[dataset['ANO_BO']=='2019']['PERIDOOCORRENCIA'].unique()

array(['A TARDE', 'A NOITE', 'PELA MANHÃ', 'DE MADRUGADA',
       'EM HORA INCERTA'], dtype=object)

In [44]:
colors = ['#034769','#3C8BB3','#88C7E6','#D3D8D7']

trace = [go.Pie(labels=dataset[dataset['ANO_BO']=='2019']['PERIDOOCORRENCIA'].unique()[0:4], values=dataset[dataset['ANO_BO']=='2019']['PERIDOOCORRENCIA'].value_counts()[0:4].values,
               hoverinfo='label+percent', 
               textfont=dict(size=18),
               marker=dict(colors=colors, 
                           line=dict(color='#000000', width=2)))]

layout = go.Layout(
    title='Turno do dia - Roubo de Celular (2019)'
)

fig = go.Figure(data = trace, layout = layout)

py.iplot(fig)

In [45]:
data = dataset[dataset["ANO_BO"] == '2019']

In [46]:
trace = [go.Bar(
            y = data['DESCRICAOLOCAL'].value_counts()[0:5].sort_values(ascending=True).index,
            x = data['DESCRICAOLOCAL'].value_counts()[0:5].sort_values(ascending=True).values,
            orientation='h',
            textposition = 'auto',
            marker=dict(
                color='rgb(158,202,225)',
                line=dict(
                    color='rgb(8,48,107)',
                    width=1,
                    )
                ),
            opacity=0.8
)]
           
layout = go.Layout(
    height=800,
    title='Locais das Ocorrências de Roubo de Celular em 2019',
    xaxis=dict(
        title = 'Ocorrências',
        type='log',
        ),
     yaxis=go.layout.YAxis(
     automargin=True
     )
)

fig = go.Figure(data=trace, layout=layout)

py.iplot(fig)

In [48]:
quantd = pd.Categorical(dataset[dataset['ANO_BO']=='2019']['ANO_BO'], categories=dataset[dataset['ano']=='2019']['mesano'].unique(), ordered=True)
ano_2014 = ano2014 = dataset[dataset['ano']=='2019']
qtdeCelular = ano2014[['QUANT_CELULAR','mesano']].groupby('mesano').count().reset_index()
trace = [go.Bar(
            x = ano2014['mesano'].value_counts().sort_index().index,
            y = np.array(qtdeCelular['QUANT_CELULAR']),
            textposition = 'auto',
            marker=dict(
                color='rgb(158,202,225)',
                line=dict(
                    color='rgb(8,48,107)',
                    width=1,
                    )
                ),
            opacity=0.8
)]
           
layout = go.Layout(
    title='Quantidade de celulares roubados por mês - 2019',
    yaxis=dict(
        title='Ocorrências'
        ),
)

fig = go.Figure(data=trace, layout=layout)

py.iplot(fig)

### HeatMap

A ideia era prosseguir nas análises mostrando um HeatMap de São Paulo no ano de 2014.
Entretanto ao seguir o [tutorial](https://towardsdatascience.com/data-101s-spatial-visualizations-and-analysis-in-python-with-folium-39730da2adf) não obtivemos sucesso na plotagem.

In [49]:
# df = data.dropna(subset=['LATITUDE', 'LONGITUDE']).copy()
# #df = df[df['DATAOCORRENCIA'] > "2014-01-01"]
# df['LATITUDE'] = df['LATITUDE'].str.replace(',', '').astype(np.float64)
# df['LONGITUDE'] = df['LONGITUDE'].str.replace(',', '').astype(np.float64)

# def generateBaseMap(default_location=[-23.64992751, -46.62569322], default_zoom_start=10):
#     base_map = Map(location=default_location, control_scale=True, zoom_start=default_zoom_start)
#     return base_map

# df['count'] = 1
# base_map = generateBaseMap()
# HeatMap(data=df[['LATITUDE','LONGITUDE', 'count']].groupby(['LATITUDE','LONGITUDE']).sum().reset_index(), radius=8, max_zoom=16).add_to(base_map)
# base_map

## Conclusões

* De acordo com [Metodologia](https://drive.google.com/file/d/1_CBHVulHPzLzRyCNpxGXSECVDV-u21QH/view), 60% dos BOs são abertos no próprio local da ocorrência, um dos motivos para as pessoas demorarem em média no máximo 2 dias para abertura de um BO.
* Não devemos eliminar nenhum dado(tupla) do conjunto de análise, embora o dataset possua erros de digitação (como exemplo, na coluna ANO_BO aparecer um dado no formato datetime64.
* Os meses de Março, Abril e Maio possuiram os maiores índices de crime e a maior quantidade de celulares roubados. Ao fazer uma busca(Google) por notícias desse período, nenhuma informação foi útil para correlacionar a esse evento.
* A maioria dos crimes ocorrem em vias públicas e próximos de áreas comerciais, onde o fluxo de pessoas é maior e o espaço para fuga também é maior.
* Há uma correlação quase direta entre o número de ocorrências e o número de celulares roubados (visto que podem haver menos ocorrências com número de celulares roubados maior).

## Trabalhos Futuros

* Terminar a ferramenta de web scraping levando em consideração o delay no site ao retornar os datasets.
* Ampliar a análise para dados geolocalizados.
* Incrementar a análise usando mais colunas do dataset (um total de 26 das 56.
* Realizar a análise com dados de 2019 e 2020 (até lá estamos baixando mês a mês).

## Equipe - Passa o Celular!
### Integrantes:
Everson Magalhães Cavalcante

Ítalo Ramillys Benicio Silva

Marcos Lunciel da Rocha Menezes de Carvalho

Ubiratan de Oliveira Junior


## Referências

#### Bibliotecas
1. [Numpy](https://numpy.org/doc/1.19/)
2. [Markdown](https://daringfireball.net/projects/markdown/basics)
3. [Plotly](https://plotly.com/python/)

    3.1 [BarChart](https://plotly.com/python/bar-charts/)
    
    3.2 [Horizontal BarChart](https://plotly.com/python/horizontal-bar-charts/)
    
    3.3 [LineChart](https://plotly.com/python/line-charts/)
    
    3.4 [PieChart](https://plotly.com/python/pie-charts/)
    
    
4. [Matplotlib](https://matplotlib.org/tutorials/introductory/pyplot.html)
    
    4.1 [HeatMap](https://matplotlib.org/3.1.1/gallery/images_contours_and_fields/image_annotated_heatmap.html)
    
    
5. [Seaborn](https://seaborn.pydata.org)


#### Links de sites e blogs
1. [Notebook do Criador](https://nbviewer.jupyter.org/github/LucasMorettoRodrigues/roubo_de_celular_em_SP/blob/master/Estudo_dos_Roubos_de_Celulares_na_Capital_de_São_Paulo.ipynb)
2. [GitHub do Criador](https://github.com/LucasMorettoRodrigues/roubo_de_celular_em_SP)

#### Livro Texto
Python Machine Learning, 2 ed.